Importint Libraries 

In [10]:
import os
import pandas as pd
import numpy as np
import json
import spotipy
import spotipy.oauth2 as oauth2
from spotipy.oauth2 import SpotifyOAuth,SpotifyClientCredentials
import yaml
import re
from tqdm import tqdm
import multiprocessing as mp
import time
import random
import datetime

In [11]:
stream= open("spotify.yaml")
spotify_details = yaml.safe_load(stream)
auth_manager = SpotifyClientCredentials(client_id=spotify_details['Client_id'],
                                        client_secret=spotify_details['client_secret'])
sp = spotipy.client.Spotify(auth_manager=auth_manager)

Importing the Dataset

In [3]:
"""
def loop_slices(path, num_slices=20):
  cnt = 0
  cnt1 = 0
  mpd_playlists = []
  unique_tracks= pd.DataFrame()
  filenames = os.listdir(path)
  for fname in tqdm(sorted(filenames, key=len)):
    if fname.startswith("mpd.slice.") and fname.endswith(".json"):
      cnt += 1
      fullpath = os.sep.join((path, fname))
      f = open(fullpath)
      js = f.read()
      f.close()
      current_slice = json.loads(js)
      # Create a list of all playlists
      for playlist in current_slice['playlists']:
        cnt1 +=1
        mpd_playlists.append(playlist)
        if cnt1 == 1000:
          cnt1=0
          temp=pd.DataFrame(mpd_playlists)
          temp=temp.explode('tracks')
          temp=pd.DataFrame(temp['tracks'].apply(pd.Series))
          unique_tracks=pd.concat([unique_tracks,temp],axis=0)
          unique_tracks.drop_duplicates(subset=['track_uri'],inplace=True)
          mpd_playlists = []
      if cnt == num_slices:
        break
  return unique_tracks
# Path where the json files are extracted
path = '../../../spotify_million_playlist_dataset\data'

print(path)
"""

'\ndef loop_slices(path, num_slices=20):\n  cnt = 0\n  cnt1 = 0\n  mpd_playlists = []\n  unique_tracks= pd.DataFrame()\n  filenames = os.listdir(path)\n  for fname in tqdm(sorted(filenames, key=len)):\n    if fname.startswith("mpd.slice.") and fname.endswith(".json"):\n      cnt += 1\n      fullpath = os.sep.join((path, fname))\n      f = open(fullpath)\n      js = f.read()\n      f.close()\n      current_slice = json.loads(js)\n      # Create a list of all playlists\n      for playlist in current_slice[\'playlists\']:\n        cnt1 +=1\n        mpd_playlists.append(playlist)\n        if cnt1 == 1000:\n          cnt1=0\n          temp=pd.DataFrame(mpd_playlists)\n          temp=temp.explode(\'tracks\')\n          temp=pd.DataFrame(temp[\'tracks\'].apply(pd.Series))\n          unique_tracks=pd.concat([unique_tracks,temp],axis=0)\n          unique_tracks.drop_duplicates(subset=[\'track_uri\'],inplace=True)\n          mpd_playlists = []\n      if cnt == num_slices:\n        break\n  retur

In [4]:
"""
df = loop_slices(path, num_slices=1000)
df.to_csv('data/1m.csv')
"""

"\ndf = loop_slices(path, num_slices=1000)\ndf.to_csv('data/1m.csv')\n"

In [5]:
"""
df["track_uri"] = df["track_uri"].apply(lambda x: re.findall(r'\w+$', x)[0])
df["artist_uri"] = df["artist_uri"].apply(lambda x: re.findall(r'\w+$', x)[0])
df["album_uri"] = df["album_uri"].apply(lambda x: re.findall(r'\w+$', x)[0])
"""

'\ndf["track_uri"] = df["track_uri"].apply(lambda x: re.findall(r\'\\w+$\', x)[0])\ndf["artist_uri"] = df["artist_uri"].apply(lambda x: re.findall(r\'\\w+$\', x)[0])\ndf["album_uri"] = df["album_uri"].apply(lambda x: re.findall(r\'\\w+$\', x)[0])\n'

In [12]:
df=pd.read_csv('../data/1m.csv') #Dropped all columns except ['track_uri', 'artist_uri', 'album_uri']

In [13]:
df.columns

Index(['Unnamed: 0', 'pos', 'artist_name', 'track_uri', 'artist_uri',
       'track_name', 'album_uri', 'duration_ms', 'album_name'],
      dtype='object')

In [14]:
t_uri=df["track_uri"].unique()
a_uri=df["artist_uri"].unique()

Feature Etraction

In [9]:
f = open('../data/audio_features.csv','a')
e=0
for i in tqdm(range(0,len(t_uri),20)):
    try:
     track_feature = sp.audio_features(t_uri[i:i+100])
     track_df = pd.DataFrame(track_feature)
     csv_data = track_df.to_csv(header=False,index=False)
     f.write(csv_data)
    except Exception as error:
        e+=1
        r = open("audio_features_log.txt", "a")
        r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+": "+str(error)+'\n')
        r.close()
        time.sleep(3)
        continue
r = open("audio_features_log.txt", "a")
r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+" _________________________ "+"Total Number Of Errors : "+str(e)+" _________________________ "+'\n')
r.close()
f.close()

  0%|          | 95/113115 [04:51<96:16:32,  3.07s/it]


KeyboardInterrupt: 

In [15]:
f = open('../data/track_features.csv','a')
e=0
for i in tqdm(range(0,len(t_uri),50)):
    try:
        track_features = sp.tracks(t_uri[i:i+50])
        for x in range(50):
            track_pop=pd.DataFrame([t_uri[i+x]])
            track_pop['release_date']=track_features['tracks'][x]['album']['release_date']
            track_pop['pop'] = track_features['tracks'][x]["popularity"]
            csv_data = track_pop.to_csv(header=False,index=False)
            f.write(csv_data)
    except Exception as error:
        e+=1
        r = open("track_features.txt", "a")
        r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+": "+str(error)+'\n')
        r.close()
        time.sleep(3)
        continue
r = open("track_features.txt", "a")
r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+" _________________________ "+"Total Number Of Errors : "+str(e)+" _________________________ "+'\n')
r.close()
f.close()

  0%|          | 1/45246 [00:00<4:28:01,  2.81it/s]

{'tracks': [{'album': {'album_type': 'album', 'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/2wIVse2owClT7go1WT98tk'}, 'href': 'https://api.spotify.com/v1/artists/2wIVse2owClT7go1WT98tk', 'id': '2wIVse2owClT7go1WT98tk', 'name': 'Missy Elliott', 'type': 'artist', 'uri': 'spotify:artist:2wIVse2owClT7go1WT98tk'}], 'available_markets': ['AR', 'AU', 'AT', 'BE', 'BO', 'BR', 'BG', 'CA', 'CL', 'CO', 'CR', 'CY', 'CZ', 'DK', 'DO', 'DE', 'EC', 'EE', 'SV', 'FI', 'FR', 'GR', 'GT', 'HN', 'HK', 'HU', 'IS', 'IE', 'IT', 'LV', 'LT', 'LU', 'MY', 'MT', 'MX', 'NL', 'NZ', 'NI', 'NO', 'PA', 'PY', 'PE', 'PH', 'PL', 'PT', 'SG', 'SK', 'ES', 'SE', 'CH', 'TW', 'TR', 'UY', 'US', 'GB', 'AD', 'LI', 'MC', 'ID', 'JP', 'TH', 'VN', 'RO', 'IL', 'ZA', 'SA', 'AE', 'BH', 'QA', 'OM', 'KW', 'EG', 'MA', 'DZ', 'TN', 'LB', 'JO', 'PS', 'IN', 'BY', 'KZ', 'MD', 'UA', 'AL', 'BA', 'HR', 'ME', 'MK', 'RS', 'SI', 'KR', 'BD', 'PK', 'LK', 'GH', 'KE', 'NG', 'TZ', 'UG', 'AG', 'AM', 'BS', 'BB', 'BZ', 'BT', 'BW', '

  0%|          | 2/45246 [00:00<3:47:45,  3.31it/s]

{'tracks': [{'album': {'album_type': 'album', 'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/3ao3jf5d70Tf4fPh2bnXVl'}, 'href': 'https://api.spotify.com/v1/artists/3ao3jf5d70Tf4fPh2bnXVl', 'id': '3ao3jf5d70Tf4fPh2bnXVl', 'name': 'We The Kings', 'type': 'artist', 'uri': 'spotify:artist:3ao3jf5d70Tf4fPh2bnXVl'}], 'available_markets': ['GB', 'IE'], 'external_urls': {'spotify': 'https://open.spotify.com/album/2F1hfUOuMnOxtSfrktL8VX'}, 'href': 'https://api.spotify.com/v1/albums/2F1hfUOuMnOxtSfrktL8VX', 'id': '2F1hfUOuMnOxtSfrktL8VX', 'images': [{'url': 'https://i.scdn.co/image/ab67616d0000b27328b45bfdfd877c8040de8f36', 'width': 640, 'height': 640}, {'url': 'https://i.scdn.co/image/ab67616d00001e0228b45bfdfd877c8040de8f36', 'width': 300, 'height': 300}, {'url': 'https://i.scdn.co/image/ab67616d0000485128b45bfdfd877c8040de8f36', 'width': 64, 'height': 64}], 'name': 'We The Kings', 'release_date': '2007', 'release_date_precision': 'year', 'total_tracks': 12, 'type': 

  0%|          | 4/45246 [00:01<2:58:33,  4.22it/s]

...

  0%|          | 28/45246 [00:08<3:56:56,  3.18it/s]

{'tracks': [{'album': {'album_type': 'album', 'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/50co4Is1HCEo8bhOyUWKpn'}, 'href': 'https://api.spotify.com/v1/artists/50co4Is1HCEo8bhOyUWKpn', 'id': '50co4Is1HCEo8bhOyUWKpn', 'name': 'Young Thug', 'type': 'artist', 'uri': 'spotify:artist:50co4Is1HCEo8bhOyUWKpn'}], 'available_markets': ['AR', 'AU', 'AT', 'BE', 'BO', 'BR', 'BG', 'CA', 'CL', 'CO', 'CR', 'CY', 'CZ', 'DK', 'DO', 'DE', 'EC', 'EE', 'SV', 'FI', 'FR', 'GR', 'GT', 'HN', 'HK', 'HU', 'IS', 'IE', 'IT', 'LV', 'LT', 'LU', 'MY', 'MT', 'MX', 'NL', 'NZ', 'NI', 'NO', 'PA', 'PY', 'PE', 'PH', 'PL', 'PT', 'SG', 'SK', 'ES', 'SE', 'CH', 'TW', 'TR', 'UY', 'US', 'GB', 'AD', 'LI', 'MC', 'ID', 'JP', 'TH', 'VN', 'RO', 'IL', 'ZA', 'SA', 'AE', 'BH', 'QA', 'OM', 'KW', 'EG', 'MA', 'DZ', 'TN', 'LB', 'JO', 'PS', 'IN', 'BY', 'KZ', 'MD', 'UA', 'AL', 'BA', 'HR', 'ME', 'MK', 'RS', 'SI', 'KR', 'BD', 'PK', 'LK', 'GH', 'KE', 'NG', 'TZ', 'UG', 'AG', 'AM', 'BS', 'BB', 'BZ', 'BT', 'BW', 'BF'

  0%|          | 30/45246 [00:08<3:33:58,  3.52it/s]

{'tracks': [{'album': {'album_type': 'album', 'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/0QHgL1lAIqAw0HtD7YldmP'}, 'href': 'https://api.spotify.com/v1/artists/0QHgL1lAIqAw0HtD7YldmP', 'id': '0QHgL1lAIqAw0HtD7YldmP', 'name': 'DJ Khaled', 'type': 'artist', 'uri': 'spotify:artist:0QHgL1lAIqAw0HtD7YldmP'}], 'available_markets': ['AR', 'AU', 'AT', 'BE', 'BO', 'BR', 'BG', 'CA', 'CL', 'CO', 'CR', 'CY', 'CZ', 'DK', 'DO', 'DE', 'EC', 'EE', 'SV', 'FI', 'FR', 'GR', 'GT', 'HN', 'HK', 'HU', 'IS', 'IE', 'IT', 'LV', 'LT', 'LU', 'MY', 'MT', 'MX', 'NL', 'NZ', 'NI', 'NO', 'PA', 'PY', 'PE', 'PH', 'PL', 'PT', 'SG', 'SK', 'ES', 'SE', 'CH', 'TW', 'TR', 'UY', 'GB', 'AD', 'LI', 'MC', 'ID', 'JP', 'TH', 'VN', 'RO', 'IL', 'ZA', 'MA', 'DZ', 'TN', 'IN', 'BY', 'KZ', 'MD', 'UA', 'AL', 'BA', 'HR', 'ME', 'MK', 'RS', 'SI', 'KR', 'BD', 'PK', 'LK', 'GH', 'KE', 'NG', 'TZ', 'UG', 'AG', 'AM', 'BS', 'BB', 'BZ', 'BT', 'BW', 'BF', 'CV', 'CW', 'DM', 'FJ', 'GM', 'GE', 'GD', 'GW', 'GY', 'HT', 'JM',

KeyboardInterrupt: 

In [ ]:
f = open('../data/artist_features.csv','a')
e=0
for i in tqdm(range(0,len(a_uri),50)):
    try:
        artist_features = sp.artists(a_uri[i:i+50])
        for x in range(50):
            artist_df=pd.DataFrame([a_uri[i+x]])
            artist_pop = artist_features['artists'][x]["popularity"]
            artist_genres = artist_features['artists'][x]["genres"]
            artist_df["artist_pop"] = artist_pop
            if artist_genres: 
                artist_df["genres"] = " ".join([re.sub(' ','_',i) for i in artist_genres])
            else:
              artist_df["genres"] = "unknown"
            csv_data = artist_df.to_csv(header=False,index=False)
            f.write(csv_data)
    except Exception as error:
        e+=1
        r = open("artist_features.txt", "a")
        r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+": "+str(error)+'\n')
        r.close()
        time.sleep(3)
        continue
r = open("artist_features.txt", "a")
r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+" _________________________ "+"Total Number Of Errors : "+str(e)+" _________________________ "+'\n')
r.close()
f.close()